In [4]:
import os
from pathlib import Path
# Setting the working directory to the root of the project
project_dir = Path("C:/Users/adbou/source/repos/KFHXRelatedAi/")
os.chdir(project_dir)

from Configs.GeneralPaths import SOURCEDATA
import pandas as pd

In [5]:
#loading the csv into pandas df

cleaned_deals_path = SOURCEDATA / "Cleaned_Deals.xlsx"

deals = pd.read_excel(cleaned_deals_path)

In [6]:
deals = deals.drop(columns=['Unnamed: 0'])
deals.head()

ContentId                                   Title  FK_StatusId  \
0     113815                       Off from Al Rifai            2   
1     113816                      Off from Dip n dip            2   
2     113817  Order from Dip n Dip and get  discount            1   
3     113818        Get  discount from Ellena Bakery            2   
4     113819                        Off from Talabat            1   

       Deal Type                                        Description  \
0  15 KD Voucher  Get a 15 KD discount voucher for your next onl...   
1  10 KD Voucher  Get 10 KD off on your next order from Dip n di...   
2   5KD discount          Order from Dip n Dip and get 5KD discount   
3   3KD discount                Get 3KD discount from Ellena Bakery   
4   3 KD Voucher                     Get 3KD discount from Talabat.   

                                            Location  Points Categories  
0  https://www.google.com/maps/search/al+rifai+ku...   15000        F&B  
1                                                NaN   10000        F&B  
2  https://www.google.com/maps/search/dipndip/@29...    5000        F&B  
3          https://maps.app.goo.gl/bnZXdfUbbaGFjFiJA    3000        F&B  
4              https://goo.gl/maps/5uoJEdD95W1YSpDt9    3000        F&B

In [8]:
from openai import OpenAI
client = OpenAI(api_key='sk-proj-lFCD6KXRS7R8kAaloineT3BlbkFJVlUaTzD3sIS4hzX9U0Fe')
EMBEDDING_MODEL = "text-embedding-3-small"

In [9]:
deals['TextEmbedding'] = deals['Title'] + ' ' + deals['Description'] + ' ' + deals['Categories']

deals = pd.DataFrame(deals)

In [11]:
deals.head()

ContentId                                   Title  FK_StatusId  \
0     113815                       Off from Al Rifai            2   
1     113816                      Off from Dip n dip            2   
2     113817  Order from Dip n Dip and get  discount            1   
3     113818        Get  discount from Ellena Bakery            2   
4     113819                        Off from Talabat            1   

       Deal Type                                        Description  \
0  15 KD Voucher  Get a 15 KD discount voucher for your next onl...   
1  10 KD Voucher  Get 10 KD off on your next order from Dip n di...   
2   5KD discount          Order from Dip n Dip and get 5KD discount   
3   3KD discount                Get 3KD discount from Ellena Bakery   
4   3 KD Voucher                     Get 3KD discount from Talabat.   

                                            Location  Points Categories  \
0  https://www.google.com/maps/search/al+rifai+ku...   15000        F&B   
1                                                NaN   10000        F&B   
2  https://www.google.com/maps/search/dipndip/@29...    5000        F&B   
3          https://maps.app.goo.gl/bnZXdfUbbaGFjFiJA    3000        F&B   
4              https://goo.gl/maps/5uoJEdD95W1YSpDt9    3000        F&B   

                                       TextEmbedding  
0  Off from Al Rifai Get a 15 KD discount voucher...  
1  Off from Dip n dip Get 10 KD off on your next ...  
2  Order from Dip n Dip and get  discount Order f...  
3  Get  discount from Ellena Bakery Get 3KD disco...  
4  Off from Talabat Get 3KD discount from Talabat...

In [12]:
#get embeddings

def get_Text_Embeddings(text):
    text = text.replace("\n", " ")
    print(f"Deal embedding : {client.embeddings.create(input=[text],model=EMBEDDING_MODEL).data[0].embedding} " )
    return client.embeddings.create(input=[text],model=EMBEDDING_MODEL).data[0].embedding


deals['ada_embedding'] = deals["TextEmbedding"].apply(lambda x: get_Text_Embeddings(x))

Deal embedding : [0.0036637482699006796, 0.0040904744528234005, -0.003922831732779741, 0.01173496711999178, 0.008863710798323154, 0.0028804009780287743, -0.06739833950996399, 0.05393817648291588, -0.02116561308503151, -0.01553282979875803, 0.003971600439399481, -0.06456974893808365, 0.052182503044605255, -0.008821037597954273, 0.012277519330382347, 0.025286568328738213, -0.01018656138330698, 0.007845663465559483, -0.019982973113656044, 0.08173633366823196, 0.044208820909261703, 0.0030556635465472937, 0.021494802087545395, -0.004657410550862551, 0.021372880786657333, 0.00604731822386384, -0.028773529455065727, -0.0396001823246479, 0.02955382876098156, -0.008528425358235836, -0.0036454598885029554, -0.033796705305576324, 0.01671547070145607, 0.006303353700786829, -0.018836908042430878, 0.02311636134982109, 0.013996615074574947, -0.004590353462845087, 0.04213615134358406, -0.029529444873332977, -0.01880033127963543, 0.01744700036942959, 0.005260922946035862, -0.0012062632013112307, 0.0190

In [37]:
embeddings_df = deals[['ContentId', 'ada_embedding']]


In [38]:
embeddings_df.head()

ContentId                                      ada_embedding
0     113815  [0.0036637482699006796, 0.0040904744528234005,...
1     113816  [0.006569046527147293, 0.006756171118468046, -...
2     113817  [0.004525594413280487, -0.03140182048082352, 0...
3     113818  [-0.003238065168261528, -0.08213862031698227, ...
4     113819  [-0.05140183866024017, -0.05169753357768059, 0...

In [39]:
embeddings_df.to_csv(Path(SOURCEDATA / "Deals_Embeddings.csv") , index=False)

In [44]:
import ast

deals_embeddings_new = pd.read_csv(Path(SOURCEDATA / "Deals_Embeddings.csv"))
deals_embeddings_new['ada_embedding'] = deals_embeddings_new['ada_embedding'].apply(ast.literal_eval)

deals_embeddings_new.head()

ContentId                                      ada_embedding
0     113815  [0.0036637482699006796, 0.0040904744528234005,...
1     113816  [0.006569046527147293, 0.006756171118468046, -...
2     113817  [0.004525594413280487, -0.03140182048082352, 0...
3     113818  [-0.003238065168261528, -0.08213862031698227, ...
4     113819  [-0.05140183866024017, -0.05169753357768059, 0...

In [45]:
first_row = deals_embeddings_new.iloc[0]

# Convert the ada_embedding to a list for better visualization
content_id = first_row['ContentId']
embedding = first_row['ada_embedding']

# Print the ContentId and the full embedding

print(f"Embedding: {embedding}")

Embedding: [0.0036637482699006796, 0.0040904744528234005, -0.003922831732779741, 0.01173496711999178, 0.008863710798323154, 0.0028804009780287743, -0.06739833950996399, 0.05393817648291588, -0.02116561308503151, -0.01553282979875803, 0.003971600439399481, -0.06456974893808365, 0.052182503044605255, -0.008821037597954273, 0.012277519330382347, 0.025286568328738213, -0.01018656138330698, 0.007845663465559483, -0.019982973113656044, 0.08173633366823196, 0.044208820909261703, 0.0030556635465472937, 0.021494802087545395, -0.004657410550862551, 0.021372880786657333, 0.00604731822386384, -0.028773529455065727, -0.0396001823246479, 0.02955382876098156, -0.008528425358235836, -0.0036454598885029554, -0.033796705305576324, 0.01671547070145607, 0.006303353700786829, -0.018836908042430878, 0.02311636134982109, 0.013996615074574947, -0.004590353462845087, 0.04213615134358406, -0.029529444873332977, -0.01880033127963543, 0.01744700036942959, 0.005260922946035862, -0.0012062632013112307, 0.0190807525

In [46]:
from sklearn.metrics.pairwise import cosine_similarity

def calculate_cosine_similarity(embedding, embeddings):
    similarities = cosine_similarity([embedding], embeddings)
    return similarities[0]

In [48]:
given_content_id = 113914

given_embedding = deals_embeddings_new[embeddings_df['ContentId'] == given_content_id]['ada_embedding'].values[0]
embeddings_list = deals_embeddings_new['ada_embedding'].tolist()
similarities = calculate_cosine_similarity(given_embedding, embeddings_list)

# Add similarities to the DataFrame
deals_embeddings_new['similarity'] = similarities
sorted_embeddings_df = deals_embeddings_new.sort_values(by='similarity', ascending=False)


In [50]:
top_5_similar = sorted_embeddings_df.head(5)
top_5_similar

ContentId                                      ada_embedding  similarity
99      113914  [0.020030125975608826, 0.046465951949357986, 0...    1.000000
128     113987  [-0.0054251751862466335, 0.05877016857266426, ...    0.586091
50      113865  [0.009563704952597618, 0.008882943540811539, 0...    0.555284
23      113838  [0.0023466094862669706, 0.011716996319591999, ...    0.553446
91      113906  [-0.015992645174264908, 0.01571495085954666, 0...    0.541791